In [4]:
import pandas as pd
import sklearn.datasets
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from itertools import chain, combinations, permutations
import numpy as np

In [5]:
df = pd.read_csv('../../Github/ozone/ozone_model_times.csv')

In [6]:
df

begin_sha  \
0     e950ecee512fd87a9c20c233ba6ed224acd2c6e4   
1     6035a8b7df6b622eb5bebe7814f81e349bbe7eb3   
2     b9496f9eaf0b9239fcd8b0084d859b4501ccc192   
3     e950ecee512fd87a9c20c233ba6ed224acd2c6e4   
4     55de3fb7e9ca2ba9c2f7b854aa09fcc3c2224532   
...                                        ...   
1800  d6cbb15f7a29221fcbd8f2c3bc9f5073c12c12d7   
1801  fe7f5b4ecad81dfff7d7703b69e2eec1907a4a95   
1802  af4730a54bd2bbc63d556936292ae760701b7e7f   
1803  334c6ee65bdc41d0150ad381bbed024a82ea0081   
1804  a1951003ddeac174c889212682c9c207604c19ac   

                                       end_sha  commits  additions  deletions  \
0     a01251c8113aee036fd7f229612a33c33cb5e558        1          6          3   
1     534160f96c5dae071192ddb809261ec7905ddbcd        4         60          0   
2     9b59ade990a87a5b8034dcc18be1e997b4f59578        3         72          3   
3     152cbea1bce867709afb498d55cc4f609aa3f98d        3        393        107   
4     a6ed346744c69d19c1000cb0c3ad75d9dd4fe669       38        132         23   
...                                        ...      ...        ...        ...   
1800  c04c01d85452e969ea81d1f8486271e85bff72a9        3          3          2   
1801  e01b47184818365dcb7baf528fb2d874209b6b47        7        428         47   
1802  3eb7235ca879498c2d8ebcd5fd228d6e4cb16891       20         39         35   
1803  3b89d4daac8747652ee360bac9a0ba1556f12c4f        7         69          0   
1804  7310491af7389cd391da09b2cfee7feb68f7261e        3        166          4   

      changed_files         total_time  begin_Dispensables  begin_Bloaters  \
0                 1     24978000000000                2006          1130.0   
1                 6     27174000000000                1002           565.0   
2                 2     43727000000000                1001           565.0   
3                 7    116274000000000                2006          1130.0   
4                 7    193769000000000                 996           563.0   
...             ...                ...                 ...             ...   
1800              1   9439818000000000                 734           428.0   
1801              8   5353469000000000                1462           854.0   
1802             21  10442829000000000                 727           427.0   
1803              1  29549932000000000                 886           506.0   
1804             16  25333529000000000                 751           428.0   

      begin_Change Preventers  begin_Couplers  \
0                      1130.0           734.0   
1                       565.0           367.0   
2                       565.0           365.0   
3                      1130.0           734.0   
4                       563.0           365.0   
...                       ...             ...   
1800                    428.0           241.0   
1801                    854.0           482.0   
1802                    427.0           233.0   
1803                    506.0           298.0   
1804                    428.0           241.0   

      begin_Object-Orientation Abusers  end_Dispensables  end_Bloaters  \
0                                734.0            1003.0         566.0   
1                                367.0             990.0         563.0   
2                                365.0             983.0         568.0   
3                                734.0             998.0         565.0   
4                                365.0             990.0         563.0   
...                                ...               ...           ...   
1800                             241.0               0.0           0.0   
1801                             482.0               0.0           0.0   
1802                             233.0               0.0           0.0   
1803                             298.0               0.0           0.0   
1804                             241.0               0.0           0.0   

      end_Change Preventers  end_Couplers  end_O

In [7]:
X = df.loc[:, ~df.columns.isin(['begin_sha', 'end_sha', 'begin_time', 'end_time', 'total_time' , 'timedelta' , 'formatted_duration'])]

In [8]:
def scale_data(data,columns):
    scaler = MinMaxScaler()
    scaled_data = scaler.fit_transform(data[columns])

    return pd.DataFrame(scaled_data)

In [9]:
def get_optimal_clusters(data):
    scores = []
    for n_clusters in range(2, len(data)):
        km = KMeans(n_clusters = n_clusters)
        km.fit(data)
        sil_avg = silhouette_score(data, km.labels_).round(4)
        scores.append([sil_avg , n_clusters])
    # scores.sort(reverse=True)
    # return scores[:5]
    return scores

In [10]:
def get_cluster_info(cluster_data):
    cluster_info = []
    # Replace with your time column name
    time_column = 'total_time'

    for cluster_num in cluster_data['cluster'].unique():
        cluster_subset = cluster_data[cluster_data['cluster'] == cluster_num]
        time_min = cluster_subset[time_column].min()
        time_max = cluster_subset[time_column].max()
        time_std = cluster_subset[time_column].std()
        time_minus_2std = time_min - 2 * time_std
        time_minus_1std = time_min - time_std
        time_plus_1std = time_max + time_std
        time_plus_2std = time_max + 2 * time_std
        time_avg = cluster_subset[(cluster_subset[time_column] >= time_minus_1std) & (cluster_subset[time_column] <= time_plus_1std)][time_column].mean()

        cluster_info.append({
            'cluster_num': cluster_num,
            'time_min': time_min,
            'time_max': time_max,
            'time_minus_2std': time_minus_2std,
            'time_minus_1std': time_minus_1std,
            'time_avg': time_avg,
            'time_plus_1std': time_plus_1std,
            'time_plus_2std': time_plus_2std
        })

    return cluster_info

In [ ]:
from itertools import combinations
import pandas as pd

# Step 1: Loop through combinations
def column_combinations(data_frame):
    columns = data_frame.columns
    col_combinations = []

    for r in range(1, len(columns) + 1):
        for combo in combinations(columns, r):
            col_combinations.append(combo)

    return col_combinations

# Main function
def main():
    data = X
    combinations_list = column_combinations(data)
    print('Combinations_list ::::' , combinations_list)

    results = []
    for combination in combinations_list:
        # print('DATA ::', data)
        # print('=====================')

        scaled_data = scale_data(data , data.columns)
        # print('SCALED ::', scaled_data)
        # print('====================')

        num_clusters = get_optimal_clusters(scaled_data)
        print('NUM ::', num_clusters)
        print('====================')

        num_clusters.sort()
        num_clusters = num_clusters[::-1]
        num_clusters = num_clusters[:3]

        kmeans = KMeans(n_clusters=3)
        cluster_labels = kmeans.fit_predict(X)
        df['cluster'] = cluster_labels

        clustered_data = df
        # print("CLUSTERRED DATA ::", clustered_data)
        # print('====================')

        cluster_info = get_cluster_info(clustered_data)
        # print("CL cluster_info ::" , cluster_info)
        # print('====================')


        for info in cluster_info:
            result_dict = {
                'combination': combination,
                'cluster_best': max(num_clusters[0]),
                'cluster_top_3' : num_clusters,
                # 'cluster_num': info['cluster_num'],
                # 'silhouette_score': get_optimal_clusters(scaled_data),
                # 'cluster_sort': num_clusters,
                'time_min': info['time_min'],
                'time_max': info['time_max'],
                'time_minus_2': info['time_minus_2std'],
                'time_minus_1': info['time_minus_1std'],
                'time_avg': info['time_avg'],
                'time_plus_1': info['time_plus_1std'],
                'time_plus_2': info['time_plus_2std']
            }
            results.append(result_dict)

    results_df = pd.DataFrame(results)
    results_df.to_csv('output_ozne.csv', index=False)  # Save results to CSV

if __name__ == "__main__":
    main()

Combinations_list :::: [('commits',), ('additions',), ('deletions',), ('changed_files',), ('begin_Dispensables',), ('begin_Bloaters',), ('begin_Change Preventers',), ('begin_Couplers',), ('begin_Object-Orientation Abusers',), ('end_Dispensables',), ('end_Bloaters',), ('end_Change Preventers',), ('end_Couplers',), ('end_Object-Orientation Abusers',), ('commits', 'additions'), ('commits', 'deletions'), ('commits', 'changed_files'), ('commits', 'begin_Dispensables'), ('commits', 'begin_Bloaters'), ('commits', 'begin_Change Preventers'), ('commits', 'begin_Couplers'), ('commits', 'begin_Object-Orientation Abusers'), ('commits', 'end_Dispensables'), ('commits', 'end_Bloaters'), ('commits', 'end_Change Preventers'), ('commits', 'end_Couplers'), ('commits', 'end_Object-Orientation Abusers'), ('additions', 'deletions'), ('additions', 'changed_files'), ('additions', 'begin_Dispensables'), ('additions', 'begin_Bloaters'), ('additions', 'begin_Change Preventers'), ('additions', 'begin_Couplers'),

C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly t

NUM :: [[0.5939, 2], [0.7352, 3], [0.774, 4], [0.8046, 5], [0.8079, 6], [0.7389, 7], [0.6425, 8], [0.6393, 9], [0.6404, 10], [0.643, 11], [0.64, 12], [0.6382, 13], [0.628, 14], [0.6305, 15], [0.635, 16], [0.6441, 17], [0.6434, 18], [0.6483, 19], [0.6532, 20], [0.658, 21], [0.6613, 22], [0.6542, 23], [0.6379, 24], [0.6365, 25], [0.633, 26], [0.6451, 27], [0.632, 28], [0.6294, 29], [0.6301, 30], [0.6235, 31], [0.6179, 32], [0.593, 33], [0.571, 34], [0.6314, 35], [0.6318, 36], [0.5863, 37], [0.6122, 38], [0.5458, 39], [0.5663, 40], [0.5925, 41], [0.589, 42], [0.5699, 43], [0.573, 44], [0.5398, 45], [0.5522, 46], [0.5177, 47], [0.5342, 48], [0.5272, 49], [0.5449, 50], [0.481, 51], [0.5437, 52], [0.512, 53], [0.4969, 54], [0.5317, 55], [0.5198, 56], [0.4849, 57], [0.4855, 58], [0.5087, 59], [0.501, 60], [0.5054, 61], [0.5039, 62], [0.4966, 63], [0.5019, 64], [0.4958, 65], [0.5071, 66], [0.5018, 67], [0.4964, 68], [0.4895, 69], [0.4921, 70], [0.5082, 71], [0.4921, 72], [0.482, 73], [0.4955, 

C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly t

NUM :: [[0.5939, 2], [0.7352, 3], [0.774, 4], [0.8046, 5], [0.8079, 6], [0.703, 7], [0.6425, 8], [0.6393, 9], [0.6404, 10], [0.6516, 11], [0.64, 12], [0.6433, 13], [0.628, 14], [0.6458, 15], [0.6305, 16], [0.6298, 17], [0.6323, 18], [0.6444, 19], [0.6556, 20], [0.6579, 21], [0.6515, 22], [0.6552, 23], [0.6528, 24], [0.6361, 25], [0.6333, 26], [0.6339, 27], [0.6304, 28], [0.6281, 29], [0.6167, 30], [0.6073, 31], [0.6328, 32], [0.5971, 33], [0.6047, 34], [0.5827, 35], [0.5686, 36], [0.6119, 37], [0.5717, 38], [0.6084, 39], [0.5555, 40], [0.5982, 41], [0.4861, 42], [0.5369, 43], [0.5729, 44], [0.5876, 45], [0.5681, 46], [0.5755, 47], [0.5384, 48], [0.536, 49], [0.5799, 50], [0.5286, 51], [0.5365, 52], [0.5371, 53], [0.5335, 54], [0.5298, 55], [0.5445, 56], [0.504, 57], [0.4971, 58], [0.5085, 59], [0.5229, 60], [0.4859, 61], [0.5082, 62], [0.4838, 63], [0.5043, 64], [0.5084, 65], [0.4956, 66], [0.5025, 67], [0.4987, 68], [0.5215, 69], [0.4965, 70], [0.4949, 71], [0.4899, 72], [0.4677, 73],

...

C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly t

NUM :: [[0.5939, 2], [0.7352, 3], [0.774, 4], [0.8046, 5], [0.8079, 6], [0.7389, 7], [0.6425, 8], [0.6393, 9], [0.6404, 10], [0.6374, 11], [0.64, 12], [0.6367, 13], [0.6333, 14], [0.6305, 15], [0.6358, 16], [0.6434, 17], [0.6434, 18], [0.6507, 19], [0.653, 20], [0.6579, 21], [0.6613, 22], [0.6529, 23], [0.6486, 24], [0.6554, 25], [0.6498, 26], [0.6339, 27], [0.6464, 28], [0.6206, 29], [0.6318, 30], [0.6126, 31], [0.6172, 32], [0.615, 33], [0.6233, 34], [0.6181, 35], [0.5565, 36], [0.61, 37], [0.5734, 38], [0.6056, 39], [0.5805, 40], [0.5693, 41], [0.6059, 42], [0.5775, 43], [0.5126, 44], [0.5538, 45], [0.5711, 46], [0.5772, 47], [0.5485, 48], [0.5402, 49], [0.5715, 50], [0.5112, 51], [0.5382, 52], [0.5309, 53], [0.5269, 54], [0.5041, 55], [0.4964, 56], [0.534, 57], [0.5087, 58], [0.4857, 59], [0.4742, 60], [0.4881, 61], [0.4871, 62], [0.5003, 63], [0.4952, 64], [0.4811, 65], [0.4938, 66], [0.4847, 67], [0.5053, 68], [0.5128, 69], [0.4938, 70], [0.4977, 71], [0.4912, 72], [0.4975, 73], 

C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly t

NUM :: [[0.5939, 2], [0.7352, 3], [0.774, 4], [0.8046, 5], [0.8079, 6], [0.7122, 7], [0.6425, 8], [0.6393, 9], [0.6404, 10], [0.6516, 11], [0.64, 12], [0.6381, 13], [0.6281, 14], [0.6357, 15], [0.6358, 16], [0.635, 17], [0.6308, 18], [0.6507, 19], [0.6413, 20], [0.6527, 21], [0.6613, 22], [0.6552, 23], [0.6366, 24], [0.6323, 25], [0.6456, 26], [0.6294, 27], [0.6293, 28], [0.6293, 29], [0.5997, 30], [0.6344, 31], [0.6224, 32], [0.5921, 33], [0.5705, 34], [0.5749, 35], [0.5536, 36], [0.6034, 37], [0.5557, 38], [0.6128, 39], [0.5505, 40], [0.5087, 41], [0.5322, 42], [0.5989, 43], [0.5637, 44], [0.5682, 45], [0.559, 46], [0.579, 47], [0.5265, 48], [0.5542, 49], [0.5138, 50], [0.5063, 51], [0.5517, 52], [0.4987, 53], [0.4977, 54], [0.5395, 55], [0.5294, 56], [0.5081, 57], [0.5229, 58], [0.5355, 59], [0.5108, 60], [0.5254, 61], [0.4978, 62], [0.5, 63], [0.4963, 64], [0.4944, 65], [0.5069, 66], [0.5048, 67], [0.493, 68], [0.5161, 69], [0.4806, 70], [0.503, 71], [0.4717, 72], [0.4993, 73], [0.

C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
C:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly t